# Minimum Working Example#

In [9]:
from netgen.csg import *
from netgen.occ import *
import numpy as np
from ngsolve import *
from ngsolve.solvers import *
from ngsolve.webgui import Draw
from Spectral_Representation import Tensor_Power

In [10]:
geo = Box((0,0,0), (3,0.6,1))
geo.faces.name="outer"
geo.faces.Min(X).name = "fix"

mesh = Mesh(OCCGeometry(geo).GenerateMesh(maxh=0.2)).Curve(3)


Draw (mesh);

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

In [11]:
E, nu = 210, 0.2
mu  = E / 2 / (1+nu)
lam = E * nu / ((1+nu)*(1-2*nu))

def F(u):
    return Id(3) + Grad(u)


def Matrix_Power(C, n):
    eig_C = C.Eig()
    lbda_1 =  eig_C[9]
    lbda_2 =  eig_C[10]
    lbda_3 =  eig_C[11]
    N_1 = CF( (eig_C[0], eig_C[1],eig_C[2] ) )
    N_2 = CF( (eig_C[3], eig_C[4],eig_C[5] ) )
    N_3 = CF( (eig_C[6], eig_C[7],eig_C[8] ) )
    return lbda_1**n * OuterProduct(N_1, N_1) +  lbda_2**n * OuterProduct(N_2, N_2) + lbda_3**n * OuterProduct(N_3, N_3) 

Flag = 1

# 1   classical Trace(C)
# 0   Matrix Power using Spectral representation

def NeoHooke_FP(F):
    C= F.trans * F
    eig_C = C.Eig()
    if Flag:
        return 0.5*mu*((Trace(C) -3) + 2*mu/lam*Det(C)**(-lam/2/mu)-1)
    else:
        return 0.5*mu*((Trace(Matrix_Power(C, 1.0)) -3) + 2*mu/lam*Det(C)**(-lam/2/mu)-1)
    
    

In [12]:
## Minimization Principle ##
fes = VectorH1(mesh, order=2, dirichlet="fix")
u,u_test = fes.TnT()


bforce = CF( (4.0,-0.25,-0.5) )

a = BilinearForm(fes, symmetric=True)
a += Variation(NeoHooke_FP(F(u)).Compile()*dx)
a += Variation(-(bforce*u).Compile()*dx)



In [13]:
## Newton Solver ##
gfsol = GridFunction(fes)
gfsol.vec[:] = 0

NewtonMinimization(a,gfsol,linesearch=False, maxit=8,maxerr=1e-8,inverse="pardiso",printing=True)


Draw (gfsol, mesh);

Newton iteration  0
Energy:  157.4999999999998
err =  0.7769696474188846
Newton iteration  1
Energy:  157.46541098290413
err =  0.6143445928782548
Newton iteration  2
Energy:  157.26597126783938
err =  0.21491707097873297
Newton iteration  3
Energy:  157.24707622339736
err =  0.09715994950134456
Newton iteration  4
Energy:  157.242370171316
err =  0.0013348734161483375
Newton iteration  5
Energy:  157.24236928219776
err =  4.872287296116848e-06
Newton iteration  6
Energy:  157.24236928218576
err =  6.744669201022382e-11


WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

In [17]:
## Some error norms ##


_F = F(gfsol).MakeVariable()

_C= _F.trans * _F
_eig_C = _C.Eig()


_I1= Trace(_C)
_I1_MP= Trace(Matrix_Power(_C, 1.0))                 # equivalent to _eig_C[9] + _eig_C[10] + _eig_C[11]
_I1_TP= Trace(Tensor_Power(_C, 1.0)) 


L2_I1_MP= Integrate(sqrt((_I1-_I1_MP)**2), mesh)
L2_I1_TP= Integrate(sqrt((_I1-_I1_TP)**2), mesh)


print(L2_I1_MP)
print(L2_I1_TP)

# Matrix_Power and Tensor_Power yield same results #


l2_I1_F_MP= sqrt(InnerProduct((_I1.Diff(_F)-_I1_MP.Diff(_F)), (_I1.Diff(_F)-_I1_MP.Diff(_F)))).Compile()
l2_I1_F_TP= sqrt(InnerProduct((_I1.Diff(_F)-_I1_TP.Diff(_F)), (_I1.Diff(_F)-_I1_TP.Diff(_F)))).Compile()

L2_I1_F_MP= Integrate(l2_I1_F_MP, mesh)
L2_I1_F_TP= Integrate(l2_I1_F_TP, mesh)

print(L2_I1_F_MP)
print(L2_I1_F_TP)

# Huge error when appplying autodiff to built-in Eig() function #

1.671355295009514e-15
3.8206279266159153e-16
6.2753801196474575
3.5615147598593618e-12
